In [1]:
%load_ext autoreload
%autoreload 2
import numpy as np
import tensorflow.keras.backend as K
import tensorflow as tf

import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"
RUN_EAGER= False
tf.config.run_functions_eagerly(RUN_EAGER)
#tf.compat.v1.experimental.output_all_intermediates(True)

In [2]:
from src.DataImporter import DataImporter
DATA_BATCH_SIZE=16
MASK_BATCH_SIZE=32
#di = DataImporter("XOR",batch_size=DATA_BATCH_SIZE,path=None)
#di.load_data(n_train_samples=512,n_test_samples=512) # for xor
di = DataImporter("MNIST",batch_size=DATA_BATCH_SIZE,path=None)
di.load_data(digits=[3,8],use2D=False) # for mnist
di.divideKFold(4)
di.newFold(0)
di.print_summary()
di.on_epoch_start()
INPUT_SHAPE = di.data_shape
OUTPUT_SIZE = np.prod(di.output_shape)
FLIP_SIZE=2

[10:03:00] INFO: Using tf version: 2.3.0
[10:03:00] DEBUG: Loading dataset name: MNIST
[10:03:00] INFO: Dataset args: 
[10:03:00] INFO: Loading MNIST dataset.
[10:03:00] INFO: Used digits: [3, 8]
[10:03:00] DEBUG: Changing y to one-hot encoding.
[10:03:00] DEBUG: During converting labels found unique: [3 8]
[10:03:00] INFO: Converting label 3 to 0.
[10:03:00] INFO: Converting label 8 to 1.
[10:03:00] DEBUG: During converting labels found unique: [3 8]
[10:03:00] DEBUG: Converting label 3 to 0.
[10:03:00] DEBUG: Converting label 8 to 1.
[10:03:00] DEBUG: Setting kfold for k=4
[10:03:00] DEBUG: Using stratified kfold.
[10:03:00] DEBUG: Current fold set to 0
[10:03:00] DEBUG: Counted 8986/2996/1984 train/val/test samples.
[10:03:00] DEBUG: Counted 562 training batches.
[10:03:00] INFO: Number of classes: 2
[10:03:00] INFO: X shape: (11982, 784)
[10:03:00] INFO: y shape: (11982, 2)
[10:03:00] INFO: X_test shape: (1984, 784)
[10:03:00] INFO: y_test shape: (1984, 2)
[10:03:00] INFO: X_train 

In [3]:
from tensorflow import keras
from src.ModelTrainer import ModelTrainer
mt = ModelTrainer(di,MASK_BATCH_SIZE, flip_size=FLIP_SIZE,
                  s_guess=50, eager_mode=RUN_EAGER)

[10:03:00] DEBUG: Trainer found 784 features.
[10:03:00] DEBUG: N batches per mode: {'train': 562, 'val': 188, 'test': 124}


In [4]:
from tensorflow.keras import layers,models
K.clear_session()
#g_task = tf.Graph()
#with g_task.as_default():
in1 = layers.Input(INPUT_SHAPE)
in2 = layers.Input(INPUT_SHAPE)
input = layers.Concatenate(axis=1)([in1,in2])
layer = layers.Dense(units=100, activation='tanh')(input)
layer = layers.Dense(units=50, activation='tanh')(layer)
layer = layers.Dense(units=20, activation='tanh')(layer)
layer = layers.Dense(units=OUTPUT_SIZE, activation='softmax')(layer)
task_model = models.Model(inputs=[in1,in2],outputs=layer,name="task_model")
mt.loadTaskModel(task_model)

mt.compileTaskModel(keras.losses.categorical_crossentropy,
                    [keras.metrics.categorical_accuracy],-1)

[10:03:01] DEBUG: Task model inputs: [<tf.Tensor 'input_1:0' shape=(None, 784) dtype=float32>, <tf.Tensor 'input_2:0' shape=(None, 784) dtype=float32>]
[10:03:01] DEBUG: Task model output: [<tf.Tensor 'dense_3/Softmax:0' shape=(None, 2) dtype=float32>]


In [5]:
mt.fit_phase_1(max_epoch=1000,early_stop=10,
               lr_patience=4,val_freq=1)

[10:03:08] DEBUG: Init datagen for phase 1 with mode: train
[10:03:08] DEBUG: Half Mask shape: (16, 784)
[10:03:09] WARNING: From /home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/ops/summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.
[10:03:16] DEBUG: Init datagen for phase 1 with mode: val
[10:03:16] DEBUG: Half Mask shape: (16, 784)
[10:10:11] DEBUG: Task model finished at epoch number: 47


Epoch 1/1000
  1/562 [..............................] - ETA: 0s - loss: 0.7232 - categorical_accuracy: 0.5391WARNING:tensorflow:From /home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/ops/summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.
562/562 [==============================] - 10s 17ms/step - loss: 0.4339 - categorical_accuracy: 0.7945 - val_loss: 0.3737 - val_categorical_accuracy: 0.8365

In [6]:
pfs_input = layers.Input(INPUT_SHAPE)
x = layers.Dense(units=200, activation='tanh')(pfs_input)
x = layers.Dense(units=200, activation='tanh')(x)
pfs_output = layers.Dense(units=np.prod(INPUT_SHAPE), activation='linear')(x)
PFS_model = models.Model(inputs=pfs_input,outputs=pfs_output,name="PFS_model")

mt.loadPFSModel(PFS_model)
mt.compilePFSModel(use_verbose_loss=False)

[10:10:11] DEBUG: PFS  model inputs: [<tf.Tensor 'input_3:0' shape=(None, 784) dtype=float32>]
[10:10:11] DEBUG: PFS  model output: [<tf.Tensor 'dense_6/BiasAdd:0' shape=(None, 784) dtype=float32>]


In [7]:
mt.fit_phase_2(max_epoch=1000,early_stop=20,
               n_pfs_samples_in_memory=5000,
               mask_batches_per_epoch=128,
               reuse_samples=False,
               lr_patience=4)

[10:10:11] DEBUG: Init datagen for phase 2 with task network target mode: 1
[10:10:11] DEBUG: Half Mask shape: (16, 784)
[10:10:35] INFO: 

[10:10:35] INFO: tracemalloc
[10:10:35] DEBUG: <__array_function__ internals>:5: size=18.1 MiB (+18.1 MiB), count=10 (+10), average=1854 KiB
[10:10:35] DEBUG: /home/maks/Scripts/Search_Net/Search_Net_PFS/src/util.py:74: size=4704 KiB (+4704 KiB), count=11 (+11), average=428 KiB
[10:10:35] DEBUG: /home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/framework/ops.py:382: size=165 KiB (+165 KiB), count=952 (+952), average=177 B
[10:10:35] DEBUG: /home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/framework/ops.py:1912: size=109 KiB (+109 KiB), count=958 (+958), average=117 B
[10:10:35] DEBUG: /home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/numpy/lib/shape_base.py:385: size=98.1 KiB (+98.1 KiB), count=2 (+2), average=49.0 KiB
[10:10:35] DEBUG: /home/maks/miniconda3/envs/tf_2.3/lib/pyt

Epoch 1/1000
128/128 [==============================] - 1s 9ms/step - loss: 0.0666

In [8]:
mt.flip_size = 10
FLIP_SIZE = 10

In [ ]:
mt.clear_PFS_data()
mt.fit_phase_3(m_opt_period=4, operator_train_period=8,
               operator_val_period=2,search_train_period=2,
               max_counter = 20000)

[10:43:13] DEBUG: Started with m_opt with size: 42.0
[10:43:14] INFO: 

[10:43:14] INFO: 0tracemalloc
[10:43:16] DEBUG: 0: created a new m_opt with size: 38.0 and:(array([ 50,  62,  78, 106, 126, 189, 198, 296, 315, 329, 349, 418, 454,
       458, 461, 486, 487, 490, 514, 516, 521, 524, 542, 545, 550, 571,
       572, 621, 657, 661, 695, 700, 710, 725, 735, 741, 759, 773]),)
[10:43:16] DEBUG: 0: Start training epoch of the  operator.
[10:43:26] DEBUG: Cleaning callback.
[10:43:26] DEBUG: 0: Start val epoch of the  operator.
[10:43:29] DEBUG: Cleaning callback.
[10:43:29] DEBUG: 0: Start training epoch of the search net.
[10:43:29] DEBUG: Separating PFS data lists of legnth: 188
[10:43:29] DEBUG: Begin search net data loop. Samples X/y:6016 6016
[10:43:30] DEBUG: Begin search net data loop. Samples X/y:6016 6016
[10:43:30] DEBUG: Cleaning callback.
[10:43:31] INFO: 

[10:43:31] INFO: 1tracemalloc
[10:43:32] DEBUG: <__array_function__ internals>:5: size=57.2 MiB (+40.6 MiB), count=18 (+1

Epoch 48/48
188/188 [==============================] - 3s 15ms/step - loss: 0.2016 - categorical_accuracy: 0.9214

In [ ]:
base_pfs_model = mt.PFS_model.get_layer("PFS_model")

In [ ]:

m0 = np.random.binomial(1,0.2,(1,784))
#m0 = np.zeros((1,784))
imps = base_pfs_model.predict(m0)
from matplotlib import pyplot as plt
pos_idx = np.argwhere(m0>0.5)[:,1]
neg_idx = np.argwhere(m0<0.5)[:,1]

imp_pos = np.copy(imps)
imp_pos[0,neg_idx] = 0.0
imp_neg = np.copy(imps)
imp_neg[0,pos_idx] = 0.0
plt.imshow((m0).reshape((28,28)))
plt.show()
plt.figure(figsize=(5,10))
plt.subplot(321)
plt.title("Removing present features, positive")
plt.imshow(np.where(imp_pos<0,-imp_pos,0).reshape((28,28)))
plt.subplot(322)
plt.title("Removing present features, negative")
plt.imshow(np.where(imp_pos>0,imp_pos,0).reshape((28,28)))
plt.subplot(323)
plt.title("Adding features, positive")
plt.imshow(np.where(imp_neg<0,-imp_neg,0).reshape((28,28)))
plt.subplot(324)
plt.title("Adding features, negative")
plt.imshow(np.where(imp_neg>0,imp_neg,0).reshape((28,28)))
plt.subplot(325)
plt.title("Important features")
plt.imshow((np.where(imp_neg<0,-imp_neg,0)+np.where(imp_pos>0,imp_pos,0)).reshape((28,28)))
plt.subplot(326)
plt.title("Noisy features")
plt.imshow((np.where(imp_neg>0,imp_neg,0)+np.where(imp_pos<0,-imp_pos,0)).reshape((28,28)))
plt.show()
plt.title("Feature importance")
plt.imshow((imp_pos-imp_neg).reshape((28,28)))
plt.show()
plt.title("Raw feature importance")
plt.imshow((imps).reshape((28,28)))
plt.show()

In [56]:
bs = 2
half_bs = int(bs/2)
#x1 = np.random.binomial(1,0.4,(bs,10))
#x2 = np.random.normal(0,1,(bs,))
pred_val = mt.PFS_model.predict(x=[x1,x2])
loss_val = mt.PFS_model.evaluate(x=[x1,x2],y=np.empty((bs,)))

m1 = x1[:half_bs]
m2 = x1[half_bs:]
aff_features = np.abs(m1-m2)

# OLD
#y_pred = aff_features*(pred_val[half_bs:]-pred_val[:half_bs])
#print("masked y_pred",y_pred)
#full_y_pred = np.sum(y_pred,axis=1)
#full_y_pred = np.concatenate([full_y_pred,-full_y_pred],axis=0)

# NEW
aff_features = np.concat([aff_features, aff_features], axis=0)
masked_y_pred = pred_val * aff_features
full_y_pred = np.sum(masked_y_pred, axis=1)

y_true = (x2[half_bs:]-x2[:half_bs])
full_y_true = np.concatenate([y_true,-y_true],axis=0)

print("y_true",full_y_true)
print("y_pred",full_y_pred)
from tensorflow.keras.losses import mean_squared_error
print(mean_squared_error(full_y_true,full_y_pred))
print(loss_val)

1/1 [==============================] - 0s 690us/step - loss: 0.0025
masked y_pred [[-0.21235526  0.          0.         -0.         -0.         -0.
  -0.00431156 -0.         -0.         -0.        ]]
y_true [-0.26716357  0.26716357]
y_pred [-0.21666682  0.21666682]
tf.Tensor(0.0025499226, shape=(), dtype=float32)
0.0025499225594103336


In [20]:

while True:
    m0 = np.random.binomial(1,0.2,(128,784))
    #base_pfs_model.evaluate(m0,np.zeros(128))
    mt.PFS_model.fit([m0,np.zeros(128)],
                     verbose=0,epochs=1)


Exception ignored in: <function IteratorResourceDeleter.__del__ at 0x7fb6623e5e50>
Traceback (most recent call last):
  File "/home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/data/ops/iterator_ops.py", line 536, in __del__
    gen_dataset_ops.delete_iterator(
  File "/home/maks/miniconda3/envs/tf_2.3/lib/python3.8/site-packages/tensorflow/python/ops/gen_dataset_ops.py", line 1277, in delete_iterator
    _result = pywrap_tfe.TFE_Py_FastPathExecute(
KeyboardInterrupt: 


KeyboardInterrupt: 

In [ ]:
gc.get_referrers(mt.PFS_y_true)